In [1]:
import pandas as pd
import numpy as np
import csv
import ast

import geopy
from geopy.geocoders import Nominatim
locator = Nominatim(user_agent= 'starczyn@uw.edu')
from geopy.extra.rate_limiter import RateLimiter
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)

import plotly.express as px
import folium
from folium import Map
from folium.plugins import HeatMap
from IPython.display import Image

In [2]:
data = pd.read_csv('/home/starczyn/Solar-PV/data/TTS_data.csv', low_memory=False)

In [3]:
data.keys()

Index(['Unnamed: 0', 'dataProvider1', 'dataProvider2', 'program1ProjectID',
       'PTODate_orProxy_', 'systemSizeInDCSTC_KW_', 'totalInstalledCost___',
       'Up_FrontCashIncentive___', 'customerSegment', 'is_expansion',
       'is_multiphase', 'tracking_Y_N_', 'ground_mounted_Y_N_',
       'hostCustomerZip__4_', 'hostCustomerCity', 'state',
       'utilityServiceTerritory', 'x3rdPartyOwned_1_0_', 'installer_clean',
       'self_install_Y_N_', 'azimuth_1', 'tilt_1', 'mod_manuf1_clean',
       'mod_model1_clean', 'moduleQty_1', 'mod_manuf2_clean',
       'mod_model2_clean', 'mod_manuf3_clean', 'mod_model3_clean',
       'additionalModuleModels_Y_N_', 'mod_tech1', 'mod_tech2', 'mod_tech3',
       'mod_BIPV1', 'mod_bifacial1', 'mod_nameplate_capacity1',
       'mod_efficiency1', 'inv_manuf1_clean', 'inv_model1_clean',
       'inverterQuantity_1', 'additionalInverterModels_Y_N_', 'inv_microinv1',
       'inv_battery_hybrid1', 'inv_builtin_meter1', 'inv_outputcapacity1',
       'dc_optimi

In [4]:
data.describe()

Unnamed: 0  systemSizeInDCSTC_KW_  totalInstalledCost___  \
count  6.175800e+05          617580.000000           6.175800e+05   
mean   5.233708e+05              17.709712           4.416344e+04   
std    3.162181e+05             199.724302           3.874617e+05   
min    2.000000e+00              -1.000000          -1.000000e+00   
25%    2.902718e+05               4.875000           1.214400e+04   
50%    5.027815e+05               6.867000           2.343100e+04   
75%    8.015032e+05               9.520000           3.525600e+04   
max    1.007467e+06           35882.400000           1.111111e+08   

       Up_FrontCashIncentive___   is_expansion  is_multiphase  tracking_Y_N_  \
count              6.175800e+05  617580.000000  617580.000000  617580.000000   
mean               3.847482e+03       0.020061       0.004174      -0.469743   
std                5.288272e+04       0.140208       0.064474       0.505051   
min               -1.000000e+00       0.000000       0.000000      -1.000000   
25%                0.000000e+00       0.000000       0.000000      -1.000000   
50%                0.000000e+00       0.000000       0.000000       0.000000   
75%                1.879000e+03       0.000000       0.000000       0.000000   
max                6.125000e+06       1.000000       1.000000       1.000000   

       ground_mounted_Y_N_  x3rdPartyOwned_1_0_  self_install_Y_N_  ...  \
count        617580.000000        617580.000000      617580.000000  ...   
mean             -0.593343             0.332852          -0.029400  ...   
std               0.513471             0.665190           0.196924  ...   
min              -1.000000            -1.000000          -1.000000  ...   
25%              -1.000000             0.000000           0.000000  ...   
50%              -1.000000             0.000000           0.000000  ...   
75%               0.000000             1.000000           0.000000  ...   
max               1.000000             1.000000           1.000000  ...   

       mod_nameplate_capacity1  mod_efficiency1  inverterQuantity_1  \
count            617580.000000    617580.000000       617580.000000   
mean                293.172437         0.179208            6.098078   
std                  44.391516         0.021989           26.997170   
min                  10.000000         0.054687           -1.000000   
25%                 260.000000         0.160714           -1.000000   
50%                 300.000000         0.180380            1.000000   
75%                 325.000000         0.197531            5.000000   
max                 510.000000         0.227545        10080.000000   

       additionalInverterModels_Y_N_  inv_microinv1  inv_battery_hybrid1  \
count                  617580.000000  617580.000000        617580.000000   
mean                       -0.431411       0.253305            -0.168615   
std                         0.498295       0.502812             0.455385   
min                        -1.000000      -1.000000            -1.000000   
25%                        -1.000000       0.000000             0.000000   
50%                         0.000000       0.000000             0.000000   
75%                         0.000000       1.000000             0.000000   
max                         1.000000       1.000000             1.000000   

       inv_builtin_meter1  inv_outputcapacity1   dc_optimizer            ILR  
count       617580.000000        617580.000000  617580.000000  617580.000000  
mean             0.537011             6.582009       0.361407       0.459918  
std              0.558846            53.905315       0.521168       1.003017  
min             -1.000000            -1.000000      -1.000000      -1.000000  
25%              0.000000             0.290000       0.000000      -1.000000  
50%              1.000000             4.000000       0.000000       1.056000  
75%              1.000000             7.000000       1.000000       1.186047  
max              1.000000        

In [4]:
data = data.loc[data['hostCustomerCity'] != -1]
data = data.loc[data['state'] != -1]

In [5]:
data = data[['dataProvider1', 'systemSizeInDCSTC_KW_', 'totalInstalledCost___', 'hostCustomerZip__4_', 'hostCustomerCity', 'state',
       'utilityServiceTerritory', 'mod_efficiency1']]
data

dataProvider1  systemSizeInDCSTC_KW_  \
0          Arizona Public Service                 12.025   
1          Arizona Public Service                  8.640   
2          Arizona Public Service                  2.400   
3          Arizona Public Service                  2.160   
4          Arizona Public Service                  2.520   
...                           ...                    ...   
617575  Wisconsin Focus on Energy                 16.060   
617576  Wisconsin Focus on Energy                 10.370   
617577  Wisconsin Focus on Energy                 13.860   
617578  Wisconsin Focus on Energy                  6.820   
617579  Wisconsin Focus on Energy                 15.410   

        totalInstalledCost___ hostCustomerZip__4_ hostCustomerCity state  \
0                       -1.00               85338         Goodyear    AZ   
1                       -1.00               85396          Buckeye    AZ   
2                       -1.00               85266       Scottsdale    AZ   
3                       -1.00               85615         Hereford    AZ   
4                       -1.00               86327            Dewey    AZ   
...                       ...                 ...              ...   ...   
617575               38320.00          53014-1214          Chilton    WI   
617576               43039.36          53072-4736         Pewaukee    WI   
617577               52360.00          53575-2219           Oregon    WI   
617578               25583.00          53559-8919         Marshall    WI   
617579               70909.00          53095-9524        West Bend    WI   

                                  utilityServiceTerritory  mod_efficiency1  
0                                  Arizona Public Service         0.199387  
1                                  Arizona Public Service         0.196262  
2                                  Arizona Public Service         0.127077  
3                                  Arizona Public Service         0.134752  
4                                  Arizona Public Service         0.145833  
...                                                   ...              ...  
617575         Wisconsin Public Service Corporation - 192         0.217262  
617576  Wisconsin Electric Power Company (WE Energies)...         0.193038  
617577          Wisconsin Power and Light (Alliant) - 191         0.196429  
617578  Wisconsin Electric Power Company (WE Energies)...         0.192803  
617579  Wisconsin Electric Power Company (WE Energies)...         0.203190  

[617580 rows x 8 columns]

In [6]:
data['city_state_country'] = data['hostCustomerCity'] + ', ' + data['state'] + ', USA'

In [230]:
#data_samp=data_samp.reset_index()
data.loc[9]

dataProvider1              Arizona Public Service
systemSizeInDCSTC_KW_                         2.0
totalInstalledCost___                        -1.0
hostCustomerZip__4_                         85032
hostCustomerCity                          Phoenix
state                                          AZ
utilityServiceTerritory    Arizona Public Service
mod_efficiency1                          0.134409
city_state_country               Phoenix, AZ, USA
Name: 9, dtype: object

In [224]:
geocode_csv = '/home/starczyn/Solar-PV/data/TTS_data_geocoded.csv'

f = open("/home/starczyn/Solar-PV/data/TTS_data_geocoded.csv", "w")
writer = csv.DictWriter(f, fieldnames= ['geopy location', 'coordinates'])
writer.writeheader()
f.close()

In [7]:
def geocode_save(row, file='TTS_data_geocoded.csv'): #row is pandas series: index in dataframe and value of column at the row
    #print(type(row))
    #print(row.index)
    
    #current_file
    current_csv = pd.read_csv(file, index_col = 0)
    
    index = row.name
    #print('Index', index)
    loc = row['city_state_country']
    
    #length of csv is number of rows that are done
    csv_length = len(current_csv) 
    #print('CSV Length ', csv_length + 1)
    

    
        
    if index <= csv_length - 1:
        
        print('index is less than csv length, returning current csv row back')
        #print('Index', index)
        #print(current_csv.iloc[index])
        
        with open(file, 'a') as geopy_csv:
            append = csv.writer(geopy_csv)
            geopy_csv.close()

        print(current_csv.iloc[index].values[0])
        return current_csv.iloc[index].values[0]

    else:
        
        #print('index is >= csv length, getting location')

        location = geocode(loc)
        #print('Location type: ', type(location))
        print(location)

        #pandas append result to current_csv
            #location.to_csv(current_csv, mode='a')

        with open(file, 'a') as geopy_csv:
            append = csv.writer(geopy_csv)
            append.writerow(location)
            geopy_csv.close()

        return "({},{})".format(location.longitude,location.latitude)

In [251]:
data.loc[1599]

dataProvider1              Arizona Public Service
systemSizeInDCSTC_KW_                        4.29
totalInstalledCost___                        -1.0
hostCustomerZip__4_                         86332
hostCustomerCity                       Camp Verde
state                                          AZ
utilityServiceTerritory    Arizona Public Service
mod_efficiency1                          0.134921
city_state_country           Campe Verde, AZ, USA
location                                      NaN
latitude                                      NaN
longitude                                     NaN
Name: 1599, dtype: object

In [249]:
data['hostCustomerCity'].loc[1599] = data['hostCustomerCity'].loc[1599].replace('Campe Verde', 'Camp Verde')

/tmp/ipykernel_152/3691808489.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['hostCustomerCity'].loc[1599] = data['hostCustomerCity'].loc[1599].replace('Campe Verde', 'Camp Verde')


In [252]:
data['city_state_country'].loc[1599] = data['city_state_country'].loc[1599].replace('Campe Verde, AZ, USA', 
                                                                                    'Camp Verde, AZ, USA')

/tmp/ipykernel_152/1781812579.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['city_state_country'].loc[1599] = data['city_state_country'].loc[1599].replace('Campe Verde, AZ, USA',


In [256]:
data.loc[2397]

dataProvider1              Arizona Public Service
systemSizeInDCSTC_KW_                        5.98
totalInstalledCost___                        -1.0
hostCustomerZip__4_                         86326
hostCustomerCity                       Cottonwood
state                                          AZ
utilityServiceTerritory    Arizona Public Service
mod_efficiency1                          0.136905
city_state_country            Cottonwood, AZ, USA
location                                      NaN
latitude                                      NaN
longitude                                     NaN
Name: 2397, dtype: object

In [ ]:
#data_samp['location'] = data_samp.apply(geocode_save, axis = 1)
#import time



for idx, row in data.iterrows():
    
    try: 
        location = geocode_save(row)
        data.loc[idx,'location'] = location
        point = ast.literal_eval(location)
        latitude, longitude = point
    
        data.loc[idx,'latitude'] = latitude
        data.loc[idx,'longitude'] = longitude
        
    except:
        data.loc[idx,'location'] = 'NaN'
        data.loc[idx,'latitude'] = 'NaN'
        data.loc[idx,'longitude'] = 'NaN'
    
    print(idx)


index is less than csv length, returning current csv row back
(42.4620577, -72.9145734)
0
index is less than csv length, returning current csv row back
(42.4203295, -72.106275)
1
index is less than csv length, returning current csv row back
(34.2429575, -118.4854081)
2
index is less than csv length, returning current csv row back
(41.4278716, -74.1659798)
3
index is less than csv length, returning current csv row back
(42.2846395, -72.399595)
4
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
5
index is less than csv length, returning current csv row back
(33.3703197, -112.583776)
6
index is less than csv length, returning current csv row back
(29.4246002, -98.4951405)
7
index is less than csv length, returning current csv row back
(41.7620447, -72.7420399)
8
index is less than csv length, returning current csv row back
(34.5300253, -112.2412739)
9
index is less than csv length, returning current csv row back
(34.5399962, -112.4687616)
10
index i

index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
90
index is less than csv length, returning current csv row back
(34.8679599, -111.7617165)
91
index is less than csv length, returning current csv row back
(34.739489, -112.009793)
92
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
93
index is less than csv length, returning current csv row back
(34.5300253, -112.2412739)
94
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
95
index is less than csv length, returning current csv row back
(34.8679599, -111.7617165)
96
index is less than csv length, returning current csv row back
(33.4353672, -112.3576)
97
index is less than csv length, returning current csv row back
(35.1987522, -111.6518229)
98
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
99
index is less than csv length, returning current csv row back
(33.5806115, -112.23729

index is less than csv length, returning current csv row back
(34.8679599, -111.7617165)
185
index is less than csv length, returning current csv row back
(33.6657535, -112.35505216920794)
186
index is less than csv length, returning current csv row back
(34.739489, -112.009793)
187
index is less than csv length, returning current csv row back
(34.8679599, -111.7617165)
188
index is less than csv length, returning current csv row back
(34.5399962, -112.4687616)
189
index is less than csv length, returning current csv row back
(34.5399962, -112.4687616)
190
index is less than csv length, returning current csv row back
(35.1987522, -111.6518229)
191
index is less than csv length, returning current csv row back
(33.4942189, -111.9260184)
192
index is less than csv length, returning current csv row back
(33.5428006, -111.9556001)
193
index is less than csv length, returning current csv row back
(33.5428006, -111.9556001)
194
index is less than csv length, returning current csv row back
(33

index is less than csv length, returning current csv row back
(34.6100243, -112.315721)
279
index is less than csv length, returning current csv row back
(34.1498408, -114.28896)
280
index is less than csv length, returning current csv row back
(33.6290111, -112.2819337)
281
index is less than csv length, returning current csv row back
(33.5428006, -111.9556001)
282
index is less than csv length, returning current csv row back
(33.6292271, -112.3680189)
283
index is less than csv length, returning current csv row back
(33.6114269, -112.4271084)
284
index is less than csv length, returning current csv row back
(33.6292271, -112.3680189)
285
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
286
index is less than csv length, returning current csv row back
(35.1987522, -111.6518229)
287
index is less than csv length, returning current csv row back
(34.7711319, -112.0579367)
288
index is less than csv length, returning current csv row back
(33.4484367

index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
372
index is less than csv length, returning current csv row back
(33.4484367, -112.0741417)
373
index is less than csv length, returning current csv row back
(35.1987522, -111.6518229)
374
index is less than csv length, returning current csv row back
(32.665135, -114.47603157249804)
375
index is less than csv length, returning current csv row back
(32.665135, -114.47603157249804)
376
index is less than csv length, returning current csv row back
(33.4942189, -111.9260184)
377
index is less than csv length, returning current csv row back
(33.4933796, -112.3581244)
378
index is less than csv length, returning current csv row back
(33.4942189, -111.9260184)
379
index is less than csv length, returning current csv row back
(33.4942189, -111.9260184)
380
index is less than csv length, returning current csv row back
(33.6290111, -112.2819337)
381
index is less than csv length, returning current csv row b

...

Goodyear, Maricopa County, Arizona, 85395, United States
42016
Buckeye, Maricopa County, Arizona, United States
42017
Buckeye, Maricopa County, Arizona, United States
42018
Flagstaff, Coconino County, Arizona, 86001, United States
42019
Chino Valley, Yavapai County, Arizona, 86323, United States
42020
Buckeye, Maricopa County, Arizona, United States
42021
Litchfield Park, Maricopa County, Arizona, United States
42022
Buckeye, Maricopa County, Arizona, United States
42023
Chandler, Maricopa County, Arizona, 85225-7872, United States
42024
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42025
Cave Creek, Maricopa County, Arizona, United States
42026
Florence, Pinal County, Arizona, United States
42027
Goodyear, Maricopa County, Arizona, 85395, United States
42028
Coolidge, Pinal County, Arizona, 85128, United States
42029
Goodyear, Maricopa County, Arizona, 85395, United States
42030
Buckeye, Maricopa County, Arizona, United States
42031
Buckeye, Maricopa County, Arizona, Un

Yuma, Yuma County, Arizona, United States
42154
Buckeye, Maricopa County, Arizona, United States
42155
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42156
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42157
Goodyear, Maricopa County, Arizona, 85395, United States
42158
Quartzsite, La Paz County, Arizona, United States
42159
San Luis, Yuma County, Arizona, United States
42160
Sun City, Maricopa County, Arizona, 85363, United States
42161
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42162
Florence, Pinal County, Arizona, United States
42163
Surprise, Maricopa County, Arizona, 85374, United States
42164
Florence, Pinal County, Arizona, United States
42165
Prescott, Yavapai County, Arizona, United States
42166
Yuma, Yuma County, Arizona, United States
42167
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42168
Peoria, Maricopa County, Arizona, 85345, United States
42169
Prescott Valley, Yavapai County, Arizona, United States
42170


Goodyear, Maricopa County, Arizona, 85395, United States
42291
Goodyear, Maricopa County, Arizona, 85395, United States
42292
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42293
Peoria, Maricopa County, Arizona, 85345, United States
42294
Yuma, Yuma County, Arizona, United States
42295
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42296
Glendale, Maricopa County, Arizona, 85301, United States
42297
El Mirage, Maricopa County, Arizona, 85335, United States
42298
Waddell, Maricopa County, Arizona, 85388, United States
42299
Buckeye, Maricopa County, Arizona, United States
42300
Buckeye, Maricopa County, Arizona, United States
42301
Surprise, Maricopa County, Arizona, 85374, United States
42302
Surprise, Maricopa County, Arizona, 85374, United States
42303
El Mirage, Maricopa County, Arizona, 85335, United States
42304
Waddell, Maricopa County, Arizona, 85388, United States
42305
Peoria, Maricopa County, Arizona, 85345, United States
42306
Peoria, Maricopa Co

Peoria, Maricopa County, Arizona, 85345, United States
42425
Goodyear, Maricopa County, Arizona, 85395, United States
42426
Cave Creek, Maricopa County, Arizona, United States
42427
Peoria, Maricopa County, Arizona, 85345, United States
42428
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42429
Yuma, Yuma County, Arizona, United States
42430
Goodyear, Maricopa County, Arizona, 85395, United States
42431
Goodyear, Maricopa County, Arizona, 85395, United States
42432
Glendale, Maricopa County, Arizona, 85301, United States
42433
Surprise, Maricopa County, Arizona, 85374, United States
42434
Sun City, Maricopa County, Arizona, 85363, United States
42435
Prescott Valley, Yavapai County, Arizona, United States
42436
Gilbert, Maricopa County, Arizona, 85269, United States
42437
Buckeye, Maricopa County, Arizona, United States
42438
Surprise, Maricopa County, Arizona, 85374, United States
42439
Prescott Valley, Yavapai County, Arizona, United States
42440
Youngtown, Maricopa Cou

Buckeye, Maricopa County, Arizona, United States
42560
Cave Creek, Maricopa County, Arizona, United States
42561
San Luis, Yuma County, Arizona, United States
42562
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42563
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42564
Phoenix, Maricopa County, Arizona, 85004-1905, United States
42565
Litchfield Park, Maricopa County, Arizona, United States
42566
Yuma, Yuma County, Arizona, United States
42567
Yuma, Yuma County, Arizona, United States
42568
Yuma, Yuma County, Arizona, United States
42569
Prescott Valley, Yavapai County, Arizona, United States
42570
Glendale, Maricopa County, Arizona, 85301, United States
42571
Casa Grande, Pinal County, Arizona, 86122, United States
42572
Prescott Valley, Yavapai County, Arizona, United States
42573
Surprise, Maricopa County, Arizona, 85374, United States
42574
Yuma, Yuma County, Arizona, United States
42575
Glendale, Maricopa County, Arizona, 85301, United States
42576
Cot

In [ ]:
data